In [ ]:
# load data
df = spark.read.format("csv").option("header",True).load("/mnt/projectteam14/Final_Data.csv")

In [ ]:
spark.conf.set("spark.sql.repl.eagerEval.maxNumColumns",14)

In [ ]:
# count no of rows and columns 
print(" rows",df.count(), "\n","columns",len(df.columns))

 rows 51729905 
 columns 14


In [ ]:
df.show(n=10)

+---+------------+----------+-------------+-----------+-------------+------+-----------------+-----------------------+-----------------------+-------------------------+-------------+------------+----------+
|_c0|   Commodity|State Name|District Name|Market Name|      Variety| Group|Arrivals (Tonnes)|Min Price (Rs./Quintal)|Max Price (Rs./Quintal)|Modal Price (Rs./Quintal)|Reported Date|Unnamed: 0.1|Unnamed: 0|
+---+------------+----------+-------------+-----------+-------------+------+-----------------+-----------------------+-----------------------+-------------------------+-------------+------------+----------+
|  0|ChennangiDal|   Gujarat|        Surat|    Songadh|        Other|Pulses|              0.5|                 5500.0|                   5905|                   5705.0|  04 Apr 2017|        NULL|      NULL|
|  1|ChennangiDal|   Gujarat|        Surat|    Songadh|   Gram Chapa|Pulses|              1.1|                 3560.0|                   3965|                   3775.0|  04

In [ ]:
# check datatypes
df.dtypes

[('_c0', 'string'),
 ('Commodity', 'string'),
 ('State Name', 'string'),
 ('District Name', 'string'),
 ('Market Name', 'string'),
 ('Variety', 'string'),
 ('Group', 'string'),
 ('Arrivals (Tonnes)', 'string'),
 ('Min Price (Rs./Quintal)', 'string'),
 ('Max Price (Rs./Quintal)', 'string'),
 ('Modal Price (Rs./Quintal)', 'string'),
 ('Reported Date', 'string'),
 ('Unnamed: 0.1', 'string'),
 ('Unnamed: 0', 'string')]

In [ ]:
# drop unnecessary columns
df = df.drop("_c0","Unnamed: 0.1","Unnamed: 0")
df

DataFrame[Commodity: string, State Name: string, District Name: string, Market Name: string, Variety: string, Group: string, Arrivals (Tonnes): string, Min Price (Rs./Quintal): string, Max Price (Rs./Quintal): string, Modal Price (Rs./Quintal): string, Reported Date: string]

In [ ]:
#checking again
df.dtypes

[('Commodity', 'string'),
 ('State Name', 'string'),
 ('District Name', 'string'),
 ('Market Name', 'string'),
 ('Variety', 'string'),
 ('Group', 'string'),
 ('Arrivals (Tonnes)', 'string'),
 ('Min Price (Rs./Quintal)', 'string'),
 ('Max Price (Rs./Quintal)', 'string'),
 ('Modal Price (Rs./Quintal)', 'string'),
 ('Reported Date', 'string')]

In [ ]:
# renaming columns 
df = df.withColumnRenamed("Min Price (Rs./Quintal)", "Min Price (Rs/Quintal)")

In [ ]:
df = df.withColumnRenamed("Max Price (Rs./Quintal)", "Max Price (Rs/Quintal)")

In [ ]:
df = df.withColumnRenamed("Modal Price (Rs./Quintal)", "Modal Price (Rs/Quintal)")

In [ ]:
df.columns

['Commodity',
 'State Name',
 'District Name',
 'Market Name',
 'Variety',
 'Group',
 'Arrivals (Tonnes)',
 'Min Price (Rs/Quintal)',
 'Max Price (Rs/Quintal)',
 'Modal Price (Rs/Quintal)',
 'Reported Date']

In [ ]:
# changing datatypes 
columns = ['Arrivals (Tonnes)','Min Price (Rs/Quintal)','Max Price (Rs/Quintal)','Modal Price (Rs/Quintal)']

from pyspark.sql.functions import col
for colname in columns:
    df = df.withColumn(colname,col(colname).cast('float'))
df.dtypes

[('Commodity', 'string'),
 ('State Name', 'string'),
 ('District Name', 'string'),
 ('Market Name', 'string'),
 ('Variety', 'string'),
 ('Group', 'string'),
 ('Arrivals (Tonnes)', 'float'),
 ('Min Price (Rs/Quintal)', 'float'),
 ('Max Price (Rs/Quintal)', 'float'),
 ('Modal Price (Rs/Quintal)', 'float'),
 ('Reported Date', 'string')]

In [ ]:
from pyspark.sql.functions import to_date
df = df.withColumn("Reported Date", to_date(col("Reported Date"), "dd MMM yyyy"))

In [ ]:
# checking again
df.dtypes

[('Commodity', 'string'),
 ('State Name', 'string'),
 ('District Name', 'string'),
 ('Market Name', 'string'),
 ('Variety', 'string'),
 ('Group', 'string'),
 ('Arrivals (Tonnes)', 'float'),
 ('Min Price (Rs/Quintal)', 'float'),
 ('Max Price (Rs/Quintal)', 'float'),
 ('Modal Price (Rs/Quintal)', 'float'),
 ('Reported Date', 'date')]

In [ ]:
# counting null values for each column
for colname in df.columns:
    nullcount = df.filter(col(colname).isNull()).count()
    print(f"{colname} : {nullcount}")

Commodity : 0
State Name : 0
District Name : 0
Market Name : 0
Variety : 0
Group : 0
Arrivals (Tonnes) : 7415990
Min Price (Rs/Quintal) : 28
Max Price (Rs/Quintal) : 112
Modal Price (Rs/Quintal) : 1057
Reported Date : 0


In [ ]:
# percentage of null values
count = df.count()
for colname in df.columns:
    nullcount = df.filter(col(colname).isNull()).count()
    percentage = (nullcount/count)*100
    print(f"{colname}: {percentage}")

Commodity: 0.0
State Name: 0.0
District Name: 0.0
Market Name: 0.0
Variety: 0.0
Group: 0.0
Arrivals (Tonnes): 14.335982252432128
Min Price (Rs/Quintal): 5.412729831999498e-05
Max Price (Rs/Quintal): 0.00021650919327997992
Modal Price (Rs/Quintal): 0.0020433055115798102
Reported Date: 0.0


In [ ]:
# filling null values
# avg min_price for each commodity
from pyspark.sql import functions as F
from pyspark.sql.functions import avg,round
avg_min = df.groupBy('Commodity').agg(round(F.avg('Min Price (Rs/Quintal)'),2).alias('avg_min'))
avg_min.show()

+------------------+--------+
|         Commodity| avg_min|
+------------------+--------+
|            Papaya| 1653.23|
|PointedgourdParval| 2719.44|
|     TenderCoconut| 4861.69|
|         Thondekai| 1501.78|
|   Pepperungarbled|43546.94|
|         Pineapple| 2367.05|
|    ChillyCapsicum| 1620.91|
|           Peascod| 2377.36|
|               Tea|15667.29|
|          ChowChow| 1494.47|
|   CinamonDalchini|  3200.0|
|            Turnip|  731.93|
|             Peach|  2301.8|
|       SkinAndHide|   165.0|
|      TamarindSeed| 1729.92|
|               Yam| 2204.19|
|     ChikoosSapota| 1674.78|
|     TubeRoseLoose|   53.01|
|              Plum| 2961.36|
|              Coca|  4400.0|
+------------------+--------+
only showing top 20 rows



In [ ]:
# checking avg_min for commodity - ChennangiDal
a = avg_min.where(avg_min["Commodity"] == "ChennangiDal")
a.show()

+------------+-------+
|   Commodity|avg_min|
+------------+-------+
|ChennangiDal| 5018.4|
+------------+-------+



In [ ]:
newdf = df.join(avg_min,on='Commodity',how='left')
newdf.show()

+------------+----------+-------------+-----------+-------------+------+-----------------+----------------------+----------------------+------------------------+-------------+-------+
|   Commodity|State Name|District Name|Market Name|      Variety| Group|Arrivals (Tonnes)|Min Price (Rs/Quintal)|Max Price (Rs/Quintal)|Modal Price (Rs/Quintal)|Reported Date|avg_min|
+------------+----------+-------------+-----------+-------------+------+-----------------+----------------------+----------------------+------------------------+-------------+-------+
|ChennangiDal|   Gujarat|        Surat|    Songadh|        Other|Pulses|              0.5|                5500.0|                5905.0|                  5705.0|   2017-04-04| 5018.4|
|ChennangiDal|   Gujarat|        Surat|    Songadh|   Gram Chapa|Pulses|              1.1|                3560.0|                3965.0|                  3775.0|   2018-04-04| 5018.4|
|ChennangiDal| Karnataka|    Bangalore|  Bangalore|Chennangi Dal|Pulses|        

In [ ]:
df = newdf.withColumn('Min Price (Rs/Quintal)',F.when(newdf['Min Price (Rs/Quintal)'].isNull(),newdf['avg_min']).otherwise(newdf['Min Price (Rs/Quintal)'])).drop('avg_min')

In [ ]:
# rechecking nullcount for Min Price (Rs/Quintal)
nc = df.filter(col('Min Price (Rs/Quintal)').isNull()).count()
nc

0

In [ ]:
# for max_price
avg_max = df.groupBy('Commodity').agg(round(F.avg('Max Price (Rs/Quintal)'),2).alias('avg_max'))
avg_max.show()

+------------------+--------+
|         Commodity| avg_max|
+------------------+--------+
|            Papaya| 1962.03|
|PointedgourdParval| 3100.59|
|     TenderCoconut| 8196.02|
|         Thondekai| 1820.63|
|   Pepperungarbled| 44392.8|
|         Pineapple| 2997.87|
|    ChillyCapsicum| 2307.65|
|           Peascod| 2965.25|
|               Tea|16985.72|
|          ChowChow| 1847.12|
|   CinamonDalchini|  3200.0|
|            Turnip|  918.92|
|             Peach| 3070.15|
|       SkinAndHide|   175.0|
|      TamarindSeed| 1912.58|
|               Yam| 2545.28|
|     ChikoosSapota| 2268.62|
|     TubeRoseLoose|   86.73|
|              Plum| 4256.34|
|              Coca|  4400.0|
+------------------+--------+
only showing top 20 rows



In [ ]:
# checking avg_max for commodity - ChennangiDal
b = avg_max.where(avg_max["Commodity"] == "ChennangiDal")
b.show()

+------------+-------+
|   Commodity|avg_max|
+------------+-------+
|ChennangiDal|5402.31|
+------------+-------+



In [ ]:
newdf2 = df.join(avg_max,on='Commodity',how='left')
newdf2.show()

+------------+----------+-------------+-----------+-------------+------+-----------------+----------------------+----------------------+------------------------+-------------+-------+
|   Commodity|State Name|District Name|Market Name|      Variety| Group|Arrivals (Tonnes)|Min Price (Rs/Quintal)|Max Price (Rs/Quintal)|Modal Price (Rs/Quintal)|Reported Date|avg_max|
+------------+----------+-------------+-----------+-------------+------+-----------------+----------------------+----------------------+------------------------+-------------+-------+
|ChennangiDal|   Gujarat|        Surat|    Songadh|        Other|Pulses|              0.5|                5500.0|                5905.0|                  5705.0|   2017-04-04|5402.31|
|ChennangiDal|   Gujarat|        Surat|    Songadh|   Gram Chapa|Pulses|              1.1|                3560.0|                3965.0|                  3775.0|   2018-04-04|5402.31|
|ChennangiDal| Karnataka|    Bangalore|  Bangalore|Chennangi Dal|Pulses|        

In [ ]:
df = newdf2.withColumn('Max Price (Rs/Quintal)',F.when(newdf2['Max Price (Rs/Quintal)'].isNull(),newdf2['avg_max']).otherwise(newdf2['Max Price (Rs/Quintal)'])).drop('avg_max')

In [ ]:
nc = df.filter(col('Max Price (Rs/Quintal)').isNull()).count()
nc

0

In [ ]:
# for modal price
avg_modal = df.groupBy('Commodity').agg(round(F.avg('Modal Price (Rs/Quintal)'),2).alias('avg_modal'))
avg_modal.show()

+------------------+---------+
|         Commodity|avg_modal|
+------------------+---------+
|            Papaya|  1862.27|
|PointedgourdParval|  2929.41|
|     TenderCoconut|  6077.33|
|         Thondekai|  1665.44|
|   Pepperungarbled| 44027.92|
|         Pineapple|  2689.41|
|    ChillyCapsicum|  1978.54|
|           Peascod|   2655.4|
|               Tea| 16630.16|
|          ChowChow|  1682.46|
|   CinamonDalchini|   3200.0|
|            Turnip|   825.43|
|             Peach|   2635.8|
|       SkinAndHide|    175.0|
|      TamarindSeed|  1817.03|
|               Yam|  2384.02|
|     ChikoosSapota|  1953.48|
|     TubeRoseLoose|    67.76|
|              Plum|  3608.41|
|              Coca|   4400.0|
+------------------+---------+
only showing top 20 rows



In [ ]:
# checking avg_modal for commodity - ChennangiDal
c = avg_modal.where(avg_modal["Commodity"] == "ChennangiDal")
c.show()

+------------+---------+
|   Commodity|avg_modal|
+------------+---------+
|ChennangiDal|  5225.89|
+------------+---------+



In [ ]:
newdf3 = df.join(avg_modal,on='Commodity',how='left')
newdf3.show()

+------------+----------+-------------+-----------+-------------+------+-----------------+----------------------+----------------------+------------------------+-------------+---------+
|   Commodity|State Name|District Name|Market Name|      Variety| Group|Arrivals (Tonnes)|Min Price (Rs/Quintal)|Max Price (Rs/Quintal)|Modal Price (Rs/Quintal)|Reported Date|avg_modal|
+------------+----------+-------------+-----------+-------------+------+-----------------+----------------------+----------------------+------------------------+-------------+---------+
|ChennangiDal|   Gujarat|        Surat|    Songadh|        Other|Pulses|              0.5|                5500.0|                5905.0|                  5705.0|   2017-04-04|  5225.89|
|ChennangiDal|   Gujarat|        Surat|    Songadh|   Gram Chapa|Pulses|              1.1|                3560.0|                3965.0|                  3775.0|   2018-04-04|  5225.89|
|ChennangiDal| Karnataka|    Bangalore|  Bangalore|Chennangi Dal|Pulse

In [ ]:
df = newdf3.withColumn('Modal Price (Rs/Quintal)',F.when(newdf3['Modal Price (Rs/Quintal)'].isNull(),newdf3['avg_modal']).otherwise(newdf3['Modal Price (Rs/Quintal)'])).drop('avg_modal')

In [ ]:
nc = df.filter(col('Modal Price (Rs/Quintal)').isNull()).count()
nc

0

In [ ]:
# for arrivals
avg_arr = df.groupBy('Commodity').agg(round(F.avg('Arrivals (Tonnes)'),2).alias('avg_arr'))
avg_arr.show()

+------------------+-------+
|         Commodity|avg_arr|
+------------------+-------+
|            Papaya|  13.22|
|PointedgourdParval|   5.82|
|     TenderCoconut| 342.72|
|         Thondekai|   6.21|
|   Pepperungarbled|   1.13|
|         Pineapple|  13.35|
|    ChillyCapsicum|   9.42|
|           Peascod|  12.51|
|               Tea|   4.08|
|          ChowChow|   2.37|
|   CinamonDalchini|   5.75|
|            Turnip|   2.22|
|             Peach|   3.78|
|       SkinAndHide|  120.0|
|      TamarindSeed|  32.77|
|               Yam|   7.35|
|     ChikoosSapota|  13.88|
|     TubeRoseLoose|  94.74|
|              Plum|   8.08|
|              Coca|    2.1|
+------------------+-------+
only showing top 20 rows



In [ ]:
# checking avg_arrival for commodity - ChennangiDal
d = avg_arr.where(avg_arr["Commodity"] == "ChennangiDal")
d.show()

+------------+-------+
|   Commodity|avg_arr|
+------------+-------+
|ChennangiDal|  24.31|
+------------+-------+



In [ ]:
newdf4 = df.join(avg_arr,on='Commodity',how='left')
newdf4.show()

+------------+----------+-------------+-----------+-------------+------+-----------------+----------------------+----------------------+------------------------+-------------+-------+
|   Commodity|State Name|District Name|Market Name|      Variety| Group|Arrivals (Tonnes)|Min Price (Rs/Quintal)|Max Price (Rs/Quintal)|Modal Price (Rs/Quintal)|Reported Date|avg_arr|
+------------+----------+-------------+-----------+-------------+------+-----------------+----------------------+----------------------+------------------------+-------------+-------+
|ChennangiDal|   Gujarat|        Surat|    Songadh|        Other|Pulses|              0.5|                5500.0|                5905.0|                  5705.0|   2017-04-04|  24.31|
|ChennangiDal|   Gujarat|        Surat|    Songadh|   Gram Chapa|Pulses|              1.1|                3560.0|                3965.0|                  3775.0|   2018-04-04|  24.31|
|ChennangiDal| Karnataka|    Bangalore|  Bangalore|Chennangi Dal|Pulses|        

In [ ]:
df = newdf4.withColumn('Arrivals (Tonnes)',F.when(newdf4['Arrivals (Tonnes)'].isNull(),newdf4['avg_arr']).otherwise(newdf4['Arrivals (Tonnes)'])).drop('avg_arr')

In [ ]:
nc = df.filter(col('Arrivals (Tonnes)').isNull()).count()
nc

483

In [ ]:
# there are 483 null values in arrivals column
nc_arr = df.filter(col("Arrivals (Tonnes)").isNull())
nc_arr.show()

+---------+------------+-------------+--------------------+----------+-------+-----------------+----------------------+----------------------+------------------------+-------------+
|Commodity|  State Name|District Name|         Market Name|   Variety|  Group|Arrivals (Tonnes)|Min Price (Rs/Quintal)|Max Price (Rs/Quintal)|Modal Price (Rs/Quintal)|Reported Date|
+---------+------------+-------------+--------------------+----------+-------+-----------------+----------------------+----------------------+------------------------+-------------+
| RoseTata|NCT of Delhi|        Delhi|Flower Market, Ca...|Rose(Tata)|Flowers|             NULL|                   1.5|                   3.5|                     2.0|   2010-01-16|
| RoseTata|NCT of Delhi|        Delhi|Flower Market, Ca...|Rose(Tata)|Flowers|             NULL|                  1.75|                  3.75|                     2.0|   2010-01-19|
| RoseTata|NCT of Delhi|        Delhi|Flower Market,Gaz...|     Other|Flowers|            

In [ ]:
# since we are getting 2 commodities that are having all null values
e = nc_arr.groupby("Commodity").count()
e.show()

+---------+-----+
|Commodity|count|
+---------+-----+
|  Jarbara|  479|
| RoseTata|    4|
+---------+-----+



In [ ]:
# avg for each commodity
grp_arr = df.groupby("Commodity").agg(round(avg("Arrivals (Tonnes)"),2).alias("avg_arrival"))
grp_arr.show()

+------------------+-----------+
|         Commodity|avg_arrival|
+------------------+-----------+
|            Papaya|      13.22|
|PointedgourdParval|       5.82|
|     TenderCoconut|     342.72|
|         Thondekai|       6.21|
|   Pepperungarbled|       1.13|
|         Pineapple|      13.35|
|    ChillyCapsicum|       9.42|
|           Peascod|      12.51|
|               Tea|       4.08|
|          ChowChow|       2.37|
|   CinamonDalchini|       5.75|
|            Turnip|       2.22|
|             Peach|       3.78|
|       SkinAndHide|      120.0|
|      TamarindSeed|      32.77|
|               Yam|       7.35|
|     ChikoosSapota|      13.88|
|     TubeRoseLoose|      94.74|
|              Plum|       8.08|
|              Coca|        2.1|
+------------------+-----------+
only showing top 20 rows



In [ ]:
# sum of all avg 
from pyspark.sql.functions import sum
tot_arr = grp_arr.agg(round(sum("avg_arrival"),2)).collect()[0][0]
tot_arrs =  float(tot_arr)
tot_arrs

11308.75

In [ ]:
# percentage of avg_arrivals 
per_avg_arr = grp_arr.withColumn('percentage',(col('avg_arrival')/tot_arrs)*100)
per_avg_arr.show()

+------------------+-----------+--------------------+
|         Commodity|avg_arrival|          percentage|
+------------------+-----------+--------------------+
|            Papaya|      13.22| 0.11690063004310822|
|PointedgourdParval|       5.82|0.051464573891897875|
|     TenderCoconut|     342.72|  3.0305736708301096|
|         Thondekai|       6.21| 0.05491323090527246|
|   Pepperungarbled|       1.13|0.009992262628495634|
|         Pineapple|      13.35| 0.11805018238089975|
|    ChillyCapsicum|       9.42| 0.08329833093843263|
|           Peascod|      12.51|  0.1106223057367083|
|               Tea|       4.08| 0.03607825798607273|
|          ChowChow|       2.37| 0.02095722338896872|
|   CinamonDalchini|       5.75| 0.05084558417154858|
|            Turnip|       2.22|0.019630816845363105|
|             Peach|       3.78|  0.0334254448988615|
|       SkinAndHide|      120.0|  1.0611252348844922|
|      TamarindSeed|      32.77| 0.28977561622637343|
|               Yam|       7

In [ ]:
from pyspark.sql.functions import round
total_sum = per_avg_arr.agg(round(sum(col("percentage")),2)).collect()[0][0]

In [ ]:
total_sum

100.0

In [ ]:
# commodity with max percentage arrivals
from pyspark.sql.functions import max
max_value = per_avg_arr.agg(max(col("percentage"))).collect()[0][0]
max_value

6.146037360450978

In [ ]:
# arrival percentage for banana
x = per_avg_arr.where(col("Commodity") == "Banana")
x.show()

+---------+-----------+-------------------+
|Commodity|avg_arrival|         percentage|
+---------+-----------+-------------------+
|   Banana|      23.77|0.21019122361003645|
+---------+-----------+-------------------+



In [ ]:
# percentage arrivals for Jarbara 
e = per_avg_arr.where(col("Commodity") == "Jarbara")
e.show()

+---------+-----------+----------+
|Commodity|avg_arrival|percentage|
+---------+-----------+----------+
|  Jarbara|       NULL|      NULL|
+---------+-----------+----------+



In [ ]:
# percentage arrivals for RoseTata 
e = per_avg_arr.where(col("Commodity") == "RoseTata")
e.show()

+---------+-----------+----------+
|Commodity|avg_arrival|percentage|
+---------+-----------+----------+
| RoseTata|       NULL|      NULL|
+---------+-----------+----------+



In [ ]:
# dropping both the commodities
df = df.filter((df['Commodity'] != "Jarbara") & (df['Commodity'] != "RoseTata"))

In [ ]:
# count of total rows 
df.count()

51729422

In [ ]:
# checking again null values 
for colname in df.columns:
    nullcount = df.filter(col(colname).isNull()).count()
    print(f"{colname} : {nullcount}")

Commodity : 0
State Name : 0
District Name : 0
Market Name : 0
Variety : 0
Group : 0
Arrivals (Tonnes) : 0
Min Price (Rs/Quintal) : 0
Max Price (Rs/Quintal) : 0
Modal Price (Rs/Quintal) : 0
Reported Date : 0


In [ ]:
df.printSchema() 

root
 |-- Commodity: string (nullable = true)
 |-- State Name: string (nullable = true)
 |-- District Name: string (nullable = true)
 |-- Market Name: string (nullable = true)
 |-- Variety: string (nullable = true)
 |-- Group: string (nullable = true)
 |-- Arrivals (Tonnes): double (nullable = true)
 |-- Min Price (Rs/Quintal): double (nullable = true)
 |-- Max Price (Rs/Quintal): double (nullable = true)
 |-- Modal Price (Rs/Quintal): double (nullable = true)
 |-- Reported Date: date (nullable = true)



In [ ]:
df.show(n=10)

+------------+----------+-------------+-----------+-------------+------+-------------------+----------------------+----------------------+------------------------+-------------+
|   Commodity|State Name|District Name|Market Name|      Variety| Group|  Arrivals (Tonnes)|Min Price (Rs/Quintal)|Max Price (Rs/Quintal)|Modal Price (Rs/Quintal)|Reported Date|
+------------+----------+-------------+-----------+-------------+------+-------------------+----------------------+----------------------+------------------------+-------------+
|ChennangiDal|   Gujarat|        Surat|    Songadh|        Other|Pulses|                0.5|                5500.0|                5905.0|                  5705.0|   2017-04-04|
|ChennangiDal|   Gujarat|        Surat|    Songadh|   Gram Chapa|Pulses|  1.100000023841858|                3560.0|                3965.0|                  3775.0|   2018-04-04|
|ChennangiDal| Karnataka|    Bangalore|  Bangalore|Chennangi Dal|Pulses|               17.0|                46

In [ ]:
# counting duplicate values 
from pyspark.sql import Window
from pyspark.sql.functions import count
w = Window.partitionBy(df.columns)
ddf = df.withColumn("duplicate_count", count("*").over(w))
duplicates_df = ddf.where(ddf["duplicate_count"] > 1)

In [ ]:
duplicates_df.count()

5150150

In [ ]:
# m = df.dropDuplicates()

In [ ]:
# m.count()

In [ ]:
df.repartition(1).write.mode("overwrite").option("header",'true').csv("/mnt/projectteam14/Final_Data")

In [ ]:
df

DataFrame[Commodity: string, State Name: string, District Name: string, Market Name: string, Variety: string, Group: string, Arrivals (Tonnes): double, Min Price (Rs/Quintal): double, Max Price (Rs/Quintal): double, Modal Price (Rs/Quintal): double, Reported Date: date]

In [ ]:
display(df)

Commodity State Name District Name Market Name Variety Group Arrivals (Tonnes) Min Price (Rs/Quintal) Max Price (Rs/Quintal) Modal Price (Rs/Quintal) Reported Date ChikoosSapota Goa North Goa Mapusa Other Fruits 0.33000001311302185 600.0 800.0 700.0 2003-04-02 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 79.0 525.0 800.0 635.0 2003-04-04 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 13.88 125.0 500.0 250.0 2003-04-04 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 70.0 550.0 745.0 600.0 2003-04-03 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 13.88 100.0 525.0 200.0 2003-04-03 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 65.0 450.0 660.0 525.0 2003-04-02 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 13.88 100.0 450.0 105.0 2003-04-02 ChikoosSapota Haryana Faridabad Faridabad Other Fruits 0.20000000298023224 1000.0 1200.0 0.0 2003-04-03 ChikoosSapota Haryana Faridabad Faridabad Other Fruits 1.2000000476837158 800.0 1000.0 0.0 2003-04-01 ChikoosSapota Haryana Sirsa Sirsa Other Fruits 1.5 650.0 1000.0 900.0 2003-04-04 ChikoosSapota Haryana Sirsa Sirsa Other Fruits 1.0 600.0 1060.0 900.0 2003-04-02 ChikoosSapota Haryana Sirsa Sirsa Other Fruits 2.0 550.0 900.0 795.0 2003-04-01 ChikoosSapota Kerala Malappuram Manjeri Other Fruits 3.0 1600.0 1600.0 1600.0 2003-04-02 ChikoosSapota Maharashtra Ahmednagar Ahmednagar Other Fruits 0.4000000059604645 400.0 900.0 650.0 2003-04-04 ChikoosSapota Maharashtra Ahmednagar Ahmednagar Other Fruits 3.5 600.0 1000.0 800.0 2003-04-03 ChikoosSapota Maharashtra Ahmednagar Ahmednagar Other Fruits 4.5 500.0 1000.0 750.0 2003-04-01 ChikoosSapota NCT of Delhi Delhi Shahdara Other Fruits 0.10000000149011612 1400.0 2000.0 1600.0 2003-04-03 ChikoosSapota NCT of Delhi Delhi Shahdara Other Fruits 13.88 1400.0 1800.0 1600.0 2003-04-02 ChikoosSapota Punjab Faridkot Faridkot Other Fruits 0.30000001192092896 830.0 1000.0 915.0 2003-04-04 ChikoosSapota Punjab Faridkot Faridkot Other Fruits 1.399999976158142 600.0 1100.0 850.0 2003-04-03 ChikoosSapota Punjab Ferozpur Firozepur City Other Fruits 5.0 600.0 800.0 700.0 2003-04-02 ChikoosSapota Punjab Gurdaspur Gurdaspur Other Fruits 1.0 800.0 800.0 800.0 2003-04-04 ChikoosSapota Punjab Gurdaspur Gurdaspur Other Fruits 0.800000011920929 500.0 700.0 600.0 2003-04-03 ChikoosSapota Punjab Gurdaspur Gurdaspur Other Fruits 13.88 600.0 700.0 650.0 2003-04-02 ChikoosSapota Punjab Gurdaspur Gurdaspur Other Fruits 0.8999999761581421 500.0 800.0 600.0 2003-04-01 ChikoosSapota Punjab Nawanshahr Nawanshahar Other Fruits 0.25 1000.0 1100.0 1050.0 2003-04-03 ChikoosSapota Punjab Fatehgarh Sirhind Other Fruits 0.20000000298023224 700.0 800.0 750.0 2003-04-04 ChikoosSapota Punjab Fatehgarh Sirhind Other Fruits 0.10000000149011612 600.0 700.0 650.0 2003-04-03 ChikoosSapota Punjab Fatehgarh Sirhind Other Fruits 0.6000000238418579 650.0 750.0 700.0 2003-04-02 ChikoosSapota Gujarat Bharuch Bharuch Other Fruits 2.0 500.0 750.0 625.0 2005-04-04 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 64.0 550.0 725.0 575.0 2005-04-04 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 13.88 295.0 545.0 325.0 2005-04-04 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 74.0 500.0 880.0 575.0 2005-04-03 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 13.88 300.0 485.0 325.0 2005-04-03 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 80.0 550.0 745.0 575.0 2005-04-02 ChikoosSapota Gujarat Navsari Chikhali Sapota Fruits 13.88 250.0 450.0 300.0 2005-04-02 ChikoosSapota Gujarat Gandhinagar Mansa Sapota Fruits 14.0 500.0 550.0 550.0 2005-04-04 ChikoosSapota Gujarat Gandhinagar Mansa Sapota Fruits 8.0 500.0 650.0 600.0 2005-04-02 ChikoosSapota Gujarat Gandhinagar Mansa Sapota Fruits 10.0 150.0 500.0 350.0 2005-04-01 ChikoosSapota Gujarat Mehsana Mehsana Other Fruits 24.219999313354492 200.0 800.0 425.0 2005-04-04 ChikoosSapota Gujarat Gandhinagar Radheja Sapota Fruits 8.0 500.0 1100.0 800.0 2005-04-04 ChikoosSapota Gujarat Valsad Valsad Other Fruits 